In [1]:
from netgen.csg import *
from ngsolve import *
from ngsolve.webgui import Draw

In [2]:
def CreateSquare():
    base = Plane(Pnt(0,0,0),Vec(0,0,1))
    surface = SplineSurface(base)
    pts = [(-0.25,-0.25,0),(-0.25,0.25,0),(0.25,0.25,0),(0.25,-0.25,0)]
    geopts = [surface.AddPoint(*p) for p in pts]
    for p1,p2,bc in [(0,1,"wire"), (1, 2,"contact"),(2,3,"wire"),(3,0,"wire")]:
        surface.AddSegment(geopts[p1],geopts[p2],bc)
    return surface

In [3]:
geo = CSGeometry()
geo.Add(Sphere(Pnt(0,0,0),1).bc("outer").mat("air"))
geo.AddSplineSurface(CreateSquare())
mesh = Mesh(geo.GenerateMesh(maxh=0.2))
Draw(mesh)

WebGuiWidget(layout=Layout(height='50vh', width='100%'), value={'gui_settings': {}, 'ngsolve_version': '6.2.24…

BaseWebGuiScene

In [4]:
fes = HCurl(mesh,order=2,complex=True)
u,v = fes.TrialFunction(), fes.TestFunction()

In [5]:
import math

mu0 = 4*math.pi*1e-7
mu = mu0
eps = 8.854*1e-12 #F/m (farad per meter)
d = 1e-3 # m diameter wire
k = 1e2 # frequency 
sigma = 1e6 # S/m

I0 = 1e3
Is = CoefficientFunction((I0,0,0)) # A

a = BilinearForm(fes)
a += SymbolicBFI(1./mu * curl(u) * curl(v) - k*k*eps * u * v)
a += SymbolicBFI(sigma * d * k * 1j * u.Trace().Trace() * v.Trace().Trace(), definedon=mesh.BBoundaries("wire"))
a += SymbolicBFI(-1j * k * sqrt(eps/mu) * u.Trace() * v.Trace(), definedon=mesh.Boundaries("outer"))

f = LinearForm(fes)
f += SymbolicLFI(Is * v.Trace().Trace(), definedon=mesh.BBoundaries("contact"))

In [6]:
u = GridFunction(fes,"u")

with TaskManager():
    a.Assemble()
    f.Assemble()
    u.vec.data = a.mat.Inverse() * f.vec

Draw(u)
Draw(curl(u),mesh,"B")

used dof inconsistency
(silence this warning by setting BilinearForm(...check_unused=False) )


Apply Inverse: PARDISO returned error -4!


WebGuiWidget(layout=Layout(height='50vh', width='100%'), value={'gui_settings': {}, 'ngsolve_version': '6.2.24…

WebGuiWidget(layout=Layout(height='50vh', width='100%'), value={'gui_settings': {}, 'ngsolve_version': '6.2.24…

BaseWebGuiScene